In [1]:
# Impoting required packages
import pandas as pd
import numpy as np
import zipfile

# setting default option
pd.set_option("mode.copy_on_write", True)

In [2]:
# View the files present in the Zip file
z = zipfile.ZipFile("../.01_Data/01_Raw/raw_mortality.zip")
z.namelist()

['Underlying Cause of Death, 2009.txt',
 '__MACOSX/',
 '__MACOSX/._Underlying Cause of Death, 2009.txt',
 'Underlying Cause of Death, 2008.txt',
 'Underlying Cause of Death, 2003.txt',
 'Underlying Cause of Death, 2014.txt',
 'Underlying Cause of Death, 2015.txt',
 'Underlying Cause of Death, 2005.txt',
 'Underlying Cause of Death, 2011.txt',
 'Underlying Cause of Death, 2010.txt',
 'Underlying Cause of Death, 2004.txt',
 'Underlying Cause of Death, 2012.txt',
 'Underlying Cause of Death, 2006.txt',
 'Underlying Cause of Death, 2007.txt',
 'Underlying Cause of Death, 2013.txt']

In [3]:
# creating list of files which start with "Underlying" so as to ignore system files
file_list = sorted([f for f in z.namelist() if f.startswith("Underlying")])
file_list

['Underlying Cause of Death, 2003.txt',
 'Underlying Cause of Death, 2004.txt',
 'Underlying Cause of Death, 2005.txt',
 'Underlying Cause of Death, 2006.txt',
 'Underlying Cause of Death, 2007.txt',
 'Underlying Cause of Death, 2008.txt',
 'Underlying Cause of Death, 2009.txt',
 'Underlying Cause of Death, 2010.txt',
 'Underlying Cause of Death, 2011.txt',
 'Underlying Cause of Death, 2012.txt',
 'Underlying Cause of Death, 2013.txt',
 'Underlying Cause of Death, 2014.txt',
 'Underlying Cause of Death, 2015.txt']

In [4]:
# read a single file to understand structure and cleaning rules required
test = pd.read_csv(z.open(file_list[0]), sep="\t")
test.sample(5)

Notes                 County  County Code    Year  Year Code  \
968    NaN        Pope County, IL      17151.0  2003.0     2003.0   
2479   NaN  Washington County, NY      36115.0  2003.0     2003.0   
1098   NaN      Warren County, IN      18171.0  2003.0     2003.0   
302    NaN   Riverside County, CA       6065.0  2003.0     2003.0   
3945   NaN  Monongalia County, WV      54061.0  2003.0     2003.0   

                     Drug/Alcohol Induced Cause  \
968   All other non-drug and non-alcohol causes   
2479  All other non-drug and non-alcohol causes   
1098  All other non-drug and non-alcohol causes   
302            All other alcohol-induced causes   
3945  All other non-drug and non-alcohol causes   

     Drug/Alcohol Induced Cause Code  Deaths  
968                               O9    34.0  
2479                              O9   640.0  
1098                              O9    91.0  
302                               A9   210.0  
3945                              O9   579.0

In [5]:
test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4102 entries, 0 to 4101
Data columns (total 8 columns):
 #   Column                           Non-Null Count  Dtype  
---  ------                           --------------  -----  
 0   Notes                            15 non-null     object 
 1   County                           4087 non-null   object 
 2   County Code                      4087 non-null   float64
 3   Year                             4087 non-null   float64
 4   Year Code                        4087 non-null   float64
 5   Drug/Alcohol Induced Cause       4087 non-null   object 
 6   Drug/Alcohol Induced Cause Code  4087 non-null   object 
 7   Deaths                           4087 non-null   float64
dtypes: float64(4), object(4)
memory usage: 256.5+ KB


In [6]:
# viewing the rows which have non-null values in Notes column
test[test["Notes"].notnull()]

Notes County  County Code  \
4087                                                ---    NaN          NaN   
4088      Dataset: Underlying Cause of Death, 1999-2017    NaN          NaN   
4089                                  Query Parameters:    NaN          NaN   
4090  Group By: County; Year; Drug/Alcohol Induced C...    NaN          NaN   
4091                              Show Totals: Disabled    NaN          NaN   
4092                         Show Zero Values: Disabled    NaN          NaN   
4093                             Show Suppressed: False    NaN          NaN   
4094                                                ---    NaN          NaN   
4095  Help: See http://wonder.cdc.gov/wonder/help/uc...    NaN          NaN   
4096                                                ---    NaN          NaN   
4097  Suggested Citation: Centers for Disease Contro...    NaN          NaN   
4098  1999-2017 on CDC WONDER Online Database, relea...    NaN          NaN   
4099  compiled from data provided by the 57 vital st...    NaN          NaN   
4100  at http://wonder.cdc.gov/ucd-icd10.html on Oct...    NaN          NaN   
4101                                                ---    NaN          NaN   

      Year  Year Code Drug/Alcohol Induced Cause  \
4087   NaN        NaN                        NaN   
4088   NaN        NaN                        NaN   
4089   NaN        NaN                        NaN   
4090   NaN        NaN                        NaN   
4091   NaN        NaN                        NaN   
4092   NaN        NaN                        NaN   
4093   NaN        NaN                        NaN   
4094   NaN        NaN                        NaN   
4095   NaN        NaN                        NaN   
4096   NaN        NaN                        NaN   
4097   NaN        NaN                        NaN   
4098   NaN        NaN                        NaN   
4099   NaN        NaN                        NaN   
4100   NaN        NaN                        NaN   
4101   NaN        NaN                        NaN   

     Drug/Alcohol Induced Cause Code  Deaths  
4087                             NaN     NaN  
4088                             NaN     NaN  
4089                             NaN     NaN  
4090                             NaN     NaN  
4091                             NaN     NaN  
4092                             NaN     NaN  
4093                             NaN     NaN  
4094                             NaN     NaN  
4095                             NaN     NaN  
4096                             NaN     NaN  
4097                             NaN     NaN  
4098                             NaN     NaN  
4099                             NaN     NaN  
4100                             NaN     NaN  
4101                             NaN     NaN

We can clean notes in a similar was as we did for the other dataset

In [7]:
# read data from all the files and append to list
df_list = []
for file in file_list:
    # read individual files
    df_temp = pd.read_csv(z.open(file), sep="\t")

    # drop the notes columns and remove rows with null values in State column
    df_temp.drop(columns=["Notes"], inplace=True)
    df_temp.dropna(subset=["County"], inplace=True)

    # add the cleaned temp Df to the main list
    df_list.append(df_temp)

In [8]:
# create the dataframe
df = pd.concat(df_list, ignore_index=True)
df.sample(5)

County  County Code    Year  Year Code  \
31806     Jones County, MS      28067.0  2010.0     2010.0   
34546  Siskiyou County, CA       6093.0  2011.0     2011.0   
53754    Tipton County, IN      18159.0  2015.0     2015.0   
6195     Wright County, MO      29229.0  2004.0     2004.0   
18249   De Soto Parish, LA      22031.0  2007.0     2007.0   

                              Drug/Alcohol Induced Cause  \
31806          All other non-drug and non-alcohol causes   
34546  Drug poisonings (overdose) Unintentional (X40-...   
53754          All other non-drug and non-alcohol causes   
6195           All other non-drug and non-alcohol causes   
18249          All other non-drug and non-alcohol causes   

      Drug/Alcohol Induced Cause Code Deaths  
31806                              O9  629.0  
34546                              D1   12.0  
53754                              O9    158  
6195                               O9  201.0  
18249                              O9  270.0

In [9]:
# check for null values
df.isnull().sum()

County                             0
County Code                        0
Year                               0
Year Code                          0
Drug/Alcohol Induced Cause         0
Drug/Alcohol Induced Cause Code    0
Deaths                             0
dtype: int64

In [10]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 57241 entries, 0 to 57240
Data columns (total 7 columns):
 #   Column                           Non-Null Count  Dtype  
---  ------                           --------------  -----  
 0   County                           57241 non-null  object 
 1   County Code                      57241 non-null  float64
 2   Year                             57241 non-null  float64
 3   Year Code                        57241 non-null  float64
 4   Drug/Alcohol Induced Cause       57241 non-null  object 
 5   Drug/Alcohol Induced Cause Code  57241 non-null  object 
 6   Deaths                           57241 non-null  object 
dtypes: float64(3), object(4)
memory usage: 3.1+ MB


In [11]:
# Cleaning the data
df2 = df.copy()

# Pad county code with 0 for consistency with other data sets
df2["County Code"] = df2["County Code"].astype(int).astype(str).str.zfill(5)

# Convert Year to Int
df2["Year"] = df2["Year"].astype(int)

# Convert Deaths to Int
df2["Deaths"] = df2["Deaths"].replace("Missing", np.nan)
df2["Deaths"] = (
    df2["Deaths"].astype(float).astype("Int64")
)  # making it as int64 so that we retain null values

In [12]:
# Check the causes of death present
df2["Drug/Alcohol Induced Cause"].unique()

array(['All other non-drug and non-alcohol causes',
       'Drug poisonings (overdose) Unintentional (X40-X44)',
       'All other alcohol-induced causes',
       'All other drug-induced causes',
       'Drug poisonings (overdose) Suicide (X60-X64)',
       'Drug poisonings (overdose) Undetermined (Y10-Y14)',
       'Alcohol poisonings (overdose) (X45, X65, Y15)',
       'Drug poisonings (overdose) Homicide (X85)'], dtype=object)

In [13]:
# Filter the data to only include drug related deaths
required_causes = [
    "Drug poisonings (overdose) Unintentional (X40-X44)",
    "All other drug-induced causes",
    "Drug poisonings (overdose) Homicide (X85)",
    "Drug poisonings (overdose) Suicide (X60-X64)",
    "Drug poisonings (overdose) Undetermined (Y10-Y14)",
]

In [14]:
df3 = df2[df2["Drug/Alcohol Induced Cause"].isin(required_causes)]

In [15]:
# remove extra columns
df3.drop(columns=["Year Code", "Drug/Alcohol Induced Cause Code"], inplace=True)

In [16]:
df3.sample(5)

County County Code  Year  \
56363    Bexar County, TX       48029  2015   
43378     Yuma County, AZ       04027  2013   
32694     Lake County, OH       39085  2010   
37892   Collin County, TX       48085  2011   
10028  Oakland County, MI       26125  2005   

                              Drug/Alcohol Induced Cause  Deaths  
56363  Drug poisonings (overdose) Unintentional (X40-...     179  
43378  Drug poisonings (overdose) Unintentional (X40-...      22  
32694  Drug poisonings (overdose) Unintentional (X40-...      39  
37892       Drug poisonings (overdose) Suicide (X60-X64)      14  
10028  Drug poisonings (overdose) Unintentional (X40-...      25

In [17]:
# renaming columns
df3.rename(
    columns={"Drug/Alcohol Induced Cause": "Cause", "County Code": "County_Code"},
    inplace=True,
)

In [18]:
# use fips file to generate proper county name and state
fips = pd.read_csv("../.01_Data/01_Raw/county_fips.csv")
fips["countyfips"] = fips["countyfips"].astype(str).str.zfill(5)

In [19]:
# merge with fips
# performing left join to get the county names
df4 = pd.merge(
    df3,
    fips,
    how="left",
    left_on="County_Code",
    right_on="countyfips",
    validate="m:1",
    indicator=True,
)
df4.sample(5)

County County_Code  Year  \
10414   Jefferson County, WI       55055  2015   
7347     Delaware County, PA       42045  2012   
5185   Williamson County, IL       17199  2010   
10403      Putnam County, WV       54079  2015   
5365      Jackson County, MO       29095  2010   

                                                   Cause  Deaths BUYER_COUNTY  \
10414  Drug poisonings (overdose) Unintentional (X40-...      10    JEFFERSON   
7347   Drug poisonings (overdose) Undetermined (Y10-Y14)      16     DELAWARE   
5185   Drug poisonings (overdose) Unintentional (X40-...      11   WILLIAMSON   
10403  Drug poisonings (overdose) Unintentional (X40-...      19       PUTNAM   
5365   Drug poisonings (overdose) Unintentional (X40-...      98      JACKSON   

      BUYER_STATE countyfips _merge  
10414          WI      55055   both  
7347           PA      42045   both  
5185           IL      17199   both  
10403          WV      54079   both  
5365           MO      29095   both

In [20]:
# Validate if merge went well
df4["_merge"].value_counts()

_merge
both          10432
left_only         0
right_only        0
Name: count, dtype: int64

In [21]:
# select required colums
df5 = df4[["BUYER_STATE", "BUYER_COUNTY", "County_Code", "Year", "Cause", "Deaths"]]

# rename columns
df5 = df5.rename(columns={"BUYER_COUNTY": "County", "BUYER_STATE": "State_Code"})

In [22]:
df5.sample(5)

State_Code    County County_Code  Year  \
4529         MI    MACOMB       26099  2009   
8646         FL     PASCO       12101  2014   
6511         TN  DAVIDSON       47037  2011   
9042         NC   HARNETT       37085  2014   
8700         ID       ADA       16001  2014   

                                                  Cause  Deaths  
4529  Drug poisonings (overdose) Undetermined (Y10-Y14)      29  
8646  Drug poisonings (overdose) Unintentional (X40-...      95  
6511  Drug poisonings (overdose) Unintentional (X40-...      91  
9042  Drug poisonings (overdose) Unintentional (X40-...      14  
8700  Drug poisonings (overdose) Unintentional (X40-...      50

In [23]:
# Add state names to maitain consistency with population data
abbreviations = pd.read_csv("../.01_Data/01_Raw/state_abbreviations.csv")
abbreviations.sample(5)

state  abbrev code
24    Mississippi   Miss.   MS
48  West Virginia   W.Va.   WV
4      California  Calif.   CA
31     New Mexico    N.M.   NM
45        Vermont     Vt.   VT

In [24]:
# rename colums to match with the main dataframe
abbreviations = abbreviations.rename(
    columns={
        "state": "State",
        "code": "State_Code",
    }
)

In [25]:
# Merge
df6 = pd.merge(
    df5,
    abbreviations[["State", "State_Code"]],
    how="left",
    on="State_Code",
    validate="m:1",
    indicator=True,
)
df6.sample(5)

State_Code      County County_Code  Year  \
1295         CA     VENTURA       06111  2005   
7659         CA      SONOMA       06097  2013   
9290         TX  MONTGOMERY       48339  2014   
5006         CA      ORANGE       06059  2010   
8888         MI     SAGINAW       26145  2014   

                                                  Cause  Deaths       State  \
1295       Drug poisonings (overdose) Suicide (X60-X64)      16  California   
7659  Drug poisonings (overdose) Unintentional (X40-...      31  California   
9290  Drug poisonings (overdose) Unintentional (X40-...      31       Texas   
5006  Drug poisonings (overdose) Unintentional (X40-...     234  California   
8888  Drug poisonings (overdose) Undetermined (Y10-Y14)      36    Michigan   

     _merge  
1295   both  
7659   both  
9290   both  
5006   both  
8888   both

In [26]:
# Validate if merge went well
df6["_merge"].value_counts()

_merge
both          10432
left_only         0
right_only        0
Name: count, dtype: int64

In script file we dont need the merge indicator column, so it will not be used there

In [27]:
# reorder columns to match population data
df6 = df6[["State", "State_Code", "County", "County_Code", "Year", "Cause", "Deaths"]]
df6.sample(5)

State State_Code        County County_Code  Year  \
2496     Tennessee         TN          KNOX       47093  2006   
2458  Pennsylvania         PA  PHILADELPHIA       42101  2006   
7091      Michigan         MI     VAN BUREN       26159  2012   
5421    New Mexico         NM      SANTA FE       35049  2010   
3975  Pennsylvania         PA    LACKAWANNA       42069  2008   

                                                  Cause  Deaths  
2496  Drug poisonings (overdose) Undetermined (Y10-Y14)      25  
2458       Drug poisonings (overdose) Suicide (X60-X64)      17  
7091  Drug poisonings (overdose) Unintentional (X40-...      10  
5421  Drug poisonings (overdose) Unintentional (X40-...      27  
3975  Drug poisonings (overdose) Unintentional (X40-...      37